# 1. Introduction

O objetivo deste projeto é extrair alguns insights sobre a venda de imóveis na King County, Washington State, USA. Os dados consistem no histórico de casas vendidas entre Maio de 2014 e Maio de 2015. Para extrair tais insights, algumas hipóteses serão testadas.

- H1: Imóveis que possuem vista para água são 30% mais caros na média. 

- H2: Imóveis com data de construção menor que 1955, são 50% mais baratos, na média. 

- H3: Imóveis sem porão possuem área total (sqft_lot) são 40% maiores do que os imóveis com porão.

- H4: O crescimento do preço dos imóveis YoY (Year Over Year) é de 10%

- H5: Imóveis com 3 banheiros tem um crescimento de MoM (Month over Month) de 15%.

# 2. Questão do Negócio

1. Quais são os imóveis que a House Rocket deveria comprar e por qual preço?
2. Qual o melhor momento para vendê-lo e por qual preço?

# 3. Entendimento do negócio 

## 3.1. Produto final

Serão entregues dois relatórios:

1. Relatório com as sugestões de compras de imóveis e valor recomendado.
2. Relatório com as sugestões de venda de um imóvel por um valor recomendado.

## 3.2. Ferramentas

- Python
- Pycharm
- Jupyter Notebook

# 4. Premissas do negócio

- Que coisiderações foram feitas ao se fazer as análises? Descrever aqui!!!!

# 5. Planejamento da solução


## 5.1. Quais são os imóveis que a House Rocket deveria comprar e por qual preço?
1. Coletar os dados no Kaggle
2. Agrupar os dados por região (zipcode)
3. Dentro de cada região, encontrar a mediana do preço dos imóveis
4. Imóveis que estão abaixo do preço mediano de cada região e que esteja, em boas condições serão comprados.
5. A planilha final terá a seguinte estrutura:

|Imóvel Cond | Região | Preço do Imóvel | Preço da Mediana | Condição | Status |
|------------|--------|-----------------|------------------|----------|--------|
|10330       |302349  |U\$ 450.000        |U\$ 500.000        |3         |Compra  |


## 5.2. Qual o melhor momento para vendê-lo e por qual preço?
1. Agrupar os imóveis por região (zipcode) e por sazonalidae (Summer, winter)
2. Dentro de cada região e sazonalidade, eu vou calcular a mediana de preço.
3. Condições de venda:
    + Se o preço da compra for maior que a mediana da região + sazonalidade.
        + O preço da venda será igual ao preço da compra + 10 %
    
    + Se o preço da compra for menor que a mediana da região + sazonalidade
        + O preço da venda será igual ao preço da compra + 30 %
    
- Exemplo da planilha de saída:

|Imóvel.Cod| Região|Temporada|Preço da Mediana |Preço da compra |Preço da venda|Lucro| Condição |
|----------| ----------|----------|----------|---------- |----------|----------| ---------- |
|10330 | 302349 | Verão | R$ 800.000,00 | R\$ 450.000,00 | R\$ 450.000,00 + 30\%| ??|

# 6. Execução da solução

## 6.1. Packages

In [76]:
import pandas as pd
import numpy as np
import plotly.express as px
from datetime import datetime
import seaborn as sns
import plotly.express as px
from statistics import mean

pd.set_option('display.float_format', lambda x: '%.3f' % x) # Modificar notação científica

## 6.2. Loading dataset

In [77]:
data = pd.read_csv('datasets/kc_house_data.csv')
data.shape

(21613, 21)

In [78]:
data.head()

id             date      price  bedrooms  bathrooms  sqft_living  \
0  7129300520  20141013T000000 221900.000         3      1.000         1180   
1  6414100192  20141209T000000 538000.000         3      2.250         2570   
2  5631500400  20150225T000000 180000.000         2      1.000          770   
3  2487200875  20141209T000000 604000.000         4      3.000         1960   
4  1954400510  20150218T000000 510000.000         3      2.000         1680   

   sqft_lot  floors  waterfront  view  ...  grade  sqft_above  sqft_basement  \
0      5650   1.000           0     0  ...      7        1180              0   
1      7242   2.000           0     0  ...      7        2170            400   
2     10000   1.000           0     0  ...      6         770              0   
3      5000   1.000           0     0  ...      7        1050            910   
4      8080   1.000           0     0  ...      8        1680              0   

   yr_built  yr_renovated  zipcode    lat     long  sqft_living15  sqft_lot15  
0      1955             0    98178 47.511 -122.257           1340        5650  
1      1951          1991    98125 47.721 -122.319           1690        7639  
2      1933             0    98028 47.738 -122.233           2720        8062  
3      1965             0    98136 47.521 -122.393           1360        5000  
4      1987             0    98074 47.617 -122.045           1800        7503  

[5 rows x 21 columns]

In [79]:
data.columns

Index(['id', 'date', 'price', 'bedrooms', 'bathrooms', 'sqft_living',
       'sqft_lot', 'floors', 'waterfront', 'view', 'condition', 'grade',
       'sqft_above', 'sqft_basement', 'yr_built', 'yr_renovated', 'zipcode',
       'lat', 'long', 'sqft_living15', 'sqft_lot15'],
      dtype='object')

In [80]:
data.dtypes

id                 int64
date              object
price            float64
bedrooms           int64
bathrooms        float64
sqft_living        int64
sqft_lot           int64
floors           float64
waterfront         int64
view               int64
condition          int64
grade              int64
sqft_above         int64
sqft_basement      int64
yr_built           int64
yr_renovated       int64
zipcode            int64
lat              float64
long             float64
sqft_living15      int64
sqft_lot15         int64
dtype: object

## 6.3. Data Transformation

In [81]:
df = data.copy()
df.head()

id             date      price  bedrooms  bathrooms  sqft_living  \
0  7129300520  20141013T000000 221900.000         3      1.000         1180   
1  6414100192  20141209T000000 538000.000         3      2.250         2570   
2  5631500400  20150225T000000 180000.000         2      1.000          770   
3  2487200875  20141209T000000 604000.000         4      3.000         1960   
4  1954400510  20150218T000000 510000.000         3      2.000         1680   

   sqft_lot  floors  waterfront  view  ...  grade  sqft_above  sqft_basement  \
0      5650   1.000           0     0  ...      7        1180              0   
1      7242   2.000           0     0  ...      7        2170            400   
2     10000   1.000           0     0  ...      6         770              0   
3      5000   1.000           0     0  ...      7        1050            910   
4      8080   1.000           0     0  ...      8        1680              0   

   yr_built  yr_renovated  zipcode    lat     long  sqft_living15  sqft_lot15  
0      1955             0    98178 47.511 -122.257           1340        5650  
1      1951          1991    98125 47.721 -122.319           1690        7639  
2      1933             0    98028 47.738 -122.233           2720        8062  
3      1965             0    98136 47.521 -122.393           1360        5000  
4      1987             0    98074 47.617 -122.045           1800        7503  

[5 rows x 21 columns]

### Transforming the variable `date` type:


In [82]:
df['date'] = pd.to_datetime(df['date'])

### Creating `month` and `year` variables:


In [83]:
df['month'] = df['date'].dt.month
df['year'] = df['date'].dt.year

### Creating `season` variable:

Seasons dates can be checked in this website: https://www.calendardate.com/year2014.php

In [84]:
df['date'].min()

Timestamp('2014-05-02 00:00:00')

In [85]:
df['date'].max()

Timestamp('2015-05-27 00:00:00')

In [86]:
# test
(df['date'][0] >= pd.to_datetime('2014-03-20')) & (df['date'][0] < pd.to_datetime('2014-06-20'))

False

In [87]:
# Creating variable `season`
df['season'] = 0

In [88]:
# Populating `season` variable
df['season'] = df['date'].apply(lambda x: 'Spring' if ((x >= pd.to_datetime('2014-03-20')) & (x < pd.to_datetime('2014-06-21'))) | ((x >= pd.to_datetime('2015-03-20')) & (x < pd.to_datetime('2015-06-20'))) else
                                          'Summer' if (x >= pd.to_datetime('2014-06-21')) & (x < pd.to_datetime('2014-09-22'))  else
                                          'Fall' if (x >= pd.to_datetime('2014-09-22')) & (x < pd.to_datetime('2014-12-21')) else
                                          'Winter'
                                          )






In [89]:
# Creating variable `old`
df['old'] = 0
df['old'] = df['yr_built'].apply(lambda x: '< 1955' if x < 1955 else
                                          '>= 1955' 
                                          )


In [90]:
df['old'].value_counts()

>= 1955    15449
< 1955      6164
Name: old, dtype: int64

In [91]:
# Creating the variable `basement` 
df['basement'] = 0
df['basement'] = df['sqft_basement'].apply(lambda x: 'Yes' if x !=0 else
                                          'No' 
                                          )

In [92]:
df['basement'].value_counts()

No     13126
Yes     8487
Name: basement, dtype: int64

### Creating `is_waterfront` variable:

In [93]:
df['is_waterfront'] = 0
df['is_waterfront'] = df['waterfront'].apply(lambda x: 'Yes' if x !=0 else
                                          'No' 
                                          )

### Grouping by zipcode and calculating median price per zipcode

In [94]:
df_price_median = df[['price', 'zipcode']].groupby('zipcode').median().reset_index()
df_price_median

zipcode       price
0     98001  260000.000
1     98002  235000.000
2     98003  267475.000
3     98004 1150000.000
4     98005  765475.000
..      ...         ...
65    98177  554000.000
66    98178  278277.000
67    98188  264000.000
68    98198  265000.000
69    98199  689800.000

[70 rows x 2 columns]

In [95]:
df_price_median = df_price_median.rename(columns = {'price': 'median_price'})

In [96]:
# Merging data frames -----------
df1 = pd.merge(df, df_price_median, on='zipcode', how='inner')
df1

id       date       price  bedrooms  bathrooms  sqft_living  \
0      7129300520 2014-10-13  221900.000         3      1.000         1180   
1      4060000240 2014-06-23  205425.000         2      1.000          880   
2      4058801670 2014-07-17  445000.000         3      2.250         2100   
3      2976800796 2014-09-25  236000.000         3      1.000         1300   
4      6874200960 2015-02-27  170000.000         2      1.000          860   
...           ...        ...         ...       ...        ...          ...   
21608  2525049086 2014-10-03 2720000.000         4      3.250         3990   
21609  2525049113 2014-07-25 1950000.000         4      3.500         4065   
21610  3262300485 2015-04-21 2250000.000         5      5.250         3410   
21611  6447300365 2014-11-13 2900000.000         5      4.000         5190   
21612  3262300818 2015-02-27 1865000.000         4      3.750         3790   

       sqft_lot  floors  waterfront  view  ...     long  sqft_living15  \
0          5650   1.000           0     0  ... -122.257           1340   
1          6780   1.000           0     0  ... -122.248           1190   
2          8201   1.000           0     2  ... -122.244           2660   
3          5898   1.000           0     0  ... -122.255           1320   
4          5265   1.000           0     0  ... -122.272           1650   
...         ...     ...         ...   ...  ...      ...            ...   
21608     18115   2.000           0     0  ... -122.229           3450   
21609     18713   2.000           0     0  ... -122.237           3070   
21610      8118   2.000           0     0  ... -122.236           3410   
21611     14600   2.000           0     1  ... -122.225           3840   
21612      8797   2.000           0     0  ... -122.236           2660   

       sqft_lot15  month  year  season      old  basement  is_waterfront  \
0            5650     10  2014    Fall  >= 1955        No             No   
1            6780      6  2014  Summer   < 1955        No             No   
2            8712      7  2014  Summer  >= 1955       Yes             No   
3            7619      9  2014    Fall  >= 1955        No             No   
4            8775      2  2015  Winter   < 1955        No             No   
...           ...    ...   ...     ...      ...       ...            ...   
21608       16087     10  2014    Fall  >= 1955        No             No   
21609       18713      7  2014  Summer  >= 1955        No             No   
21610       16236      4  2015  Spring  >= 1955        No             No   
21611       19250     11  2014    Fall  >= 1955        No             No   
21612       12150      2  2015  Winter  >= 1955       Yes             No   

       median_price  
0        278277.000  
1        278277.000  
2        278277.000  
3        278277.000  
4        278277.000  
...             ...  
21608   1892500.000  
21609   1892500.000  
21610   1892500.000  
21611   1892500.000  
21612   1892500.000  

[21613 rows x 28 columns]

## 6.4. First table: suggestions for buying

In [97]:
# Creating Status Variable -----------
df1['status'] = 0

for i in range(len(df1)):
    if(df1.loc[i, 'price'] < df1.loc[i, 'median_price']) & (df1.loc[i, 'condition'] >= 2):
        df1.loc[i, 'status'] = "buy"
    else:
        df1.loc[i, 'status'] = "do not buy"

In [98]:
df1

id       date       price  bedrooms  bathrooms  sqft_living  \
0      7129300520 2014-10-13  221900.000         3      1.000         1180   
1      4060000240 2014-06-23  205425.000         2      1.000          880   
2      4058801670 2014-07-17  445000.000         3      2.250         2100   
3      2976800796 2014-09-25  236000.000         3      1.000         1300   
4      6874200960 2015-02-27  170000.000         2      1.000          860   
...           ...        ...         ...       ...        ...          ...   
21608  2525049086 2014-10-03 2720000.000         4      3.250         3990   
21609  2525049113 2014-07-25 1950000.000         4      3.500         4065   
21610  3262300485 2015-04-21 2250000.000         5      5.250         3410   
21611  6447300365 2014-11-13 2900000.000         5      4.000         5190   
21612  3262300818 2015-02-27 1865000.000         4      3.750         3790   

       sqft_lot  floors  waterfront  view  ...  sqft_living15  sqft_lot15  \
0          5650   1.000           0     0  ...           1340        5650   
1          6780   1.000           0     0  ...           1190        6780   
2          8201   1.000           0     2  ...           2660        8712   
3          5898   1.000           0     0  ...           1320        7619   
4          5265   1.000           0     0  ...           1650        8775   
...         ...     ...         ...   ...  ...            ...         ...   
21608     18115   2.000           0     0  ...           3450       16087   
21609     18713   2.000           0     0  ...           3070       18713   
21610      8118   2.000           0     0  ...           3410       16236   
21611     14600   2.000           0     1  ...           3840       19250   
21612      8797   2.000           0     0  ...           2660       12150   

       month  year  season      old  basement  is_waterfront  median_price  \
0         10  2014    Fall  >= 1955        No             No    278277.000   
1          6  2014  Summer   < 1955        No             No    278277.000   
2          7  2014  Summer  >= 1955       Yes             No    278277.000   
3          9  2014    Fall  >= 1955        No             No    278277.000   
4          2  2015  Winter   < 1955        No             No    278277.000   
...      ...   ...     ...      ...       ...            ...           ...   
21608     10  2014    Fall  >= 1955        No             No   1892500.000   
21609      7  2014  Summer  >= 1955        No             No   1892500.000   
21610      4  2015  Spring  >= 1955        No             No   1892500.000   
21611     11  2014    Fall  >= 1955        No             No   1892500.000   
21612      2  2015  Winter  >= 1955       Yes             No   1892500.000   

           status  
0             buy  
1             buy  
2      do not buy  
3             buy  
4             buy  
...           ...  
21608  do not buy  
21609  do not buy  
21610  do not buy  
21611  do not buy  
21612         buy  

[21613 rows x 29 columns]

In [99]:
# Creating Dataframe to be delivered -----------
df2 = df1[['id', 'zipcode', 'price', 'median_price', 'condition', 'status']].copy()
df2.columns = ['ID', 'Region', 'Price', 'Median Price', 'Condition', 'Status']
df2.head()

ID  Region      Price  Median Price  Condition      Status
0  7129300520   98178 221900.000    278277.000          3         buy
1  4060000240   98178 205425.000    278277.000          4         buy
2  4058801670   98178 445000.000    278277.000          3  do not buy
3  2976800796   98178 236000.000    278277.000          3         buy
4  6874200960   98178 170000.000    278277.000          3         buy

## 6.5.  Second Table: Price suggestions for buying and selling

- Here we are going to consider only the properties with the Status equal to "buy" in this analysis. 

In [100]:
df3 = df1[df1['status'] == "buy"].copy().reset_index()
df3

index          id       date       price  bedrooms  bathrooms  \
0          0  7129300520 2014-10-13  221900.000         3      1.000   
1          1  4060000240 2014-06-23  205425.000         2      1.000   
2          3  2976800796 2014-09-25  236000.000         3      1.000   
3          4  6874200960 2015-02-27  170000.000         2      1.000   
4          5  4268200055 2015-05-01  245000.000         3      1.750   
...      ...         ...        ...         ...       ...        ...   
10708  21600  3025300225 2014-10-31 1450000.000         5      2.750   
10709  21601  2470200020 2014-05-14 1880000.000         4      2.750   
10710  21603  3625049079 2014-08-01 1350000.000         3      2.000   
10711  21605  5427100150 2014-06-26 1410000.000         4      2.250   
10712  21612  3262300818 2015-02-27 1865000.000         4      3.750   

       sqft_living  sqft_lot  floors  waterfront  ...  sqft_living15  \
0             1180      5650   1.000           0  ...           1340   
1              880      6780   1.000           0  ...           1190   
2             1300      5898   1.000           0  ...           1320   
3              860      5265   1.000           0  ...           1650   
4             1740     11547   1.000           0  ...            880   
...            ...       ...     ...         ...  ...            ...   
10708         3090     19865   1.000           0  ...           2970   
10709         3260     19542   1.000           0  ...           3480   
10710         2070      9600   1.000           0  ...           3000   
10711         3250     16684   2.000           0  ...           2890   
10712         3790      8797   2.000           0  ...           2660   

       sqft_lot15  month  year  season      old  basement  is_waterfront  \
0            5650     10  2014    Fall  >= 1955        No             No   
1            6780      6  2014  Summer   < 1955        No             No   
2            7619      9  2014    Fall  >= 1955        No             No   
3            8775      2  2015  Winter   < 1955        No             No   
4           78408      5  2015  Spring   < 1955        No             No   
...           ...    ...   ...     ...      ...       ...            ...   
10708       19862     10  2014    Fall   < 1955        No             No   
10709       19863      5  2014  Spring  >= 1955       Yes             No   
10710       16215      8  2014  Summer   < 1955       Yes             No   
10711       16927      6  2014  Summer  >= 1955        No             No   
10712       12150      2  2015  Winter  >= 1955       Yes             No   

       median_price  status  
0        278277.000     buy  
1        278277.000     buy  
2        278277.000     buy  
3        278277.000     buy  
4        278277.000     buy  
...             ...     ...  
10708   1892500.000     buy  
10709   1892500.000     buy  
10710   1892500.000     buy  
10711   1892500.000     buy  
10712   1892500.000     buy  

[10713 rows x 30 columns]

### Grouping by zipcode and season

In [101]:
df4 = df3[['price', 'zipcode', 'season']].groupby(['zipcode', 'season']).median().reset_index()
df4.columns = ['zipcode', 'season', 'median_price_zipcode_season']
df4

zipcode  season  median_price_zipcode_season
0      98001    Fall                   215000.000
1      98001  Spring                   214550.000
2      98001  Summer                   215000.000
3      98001  Winter                   218500.000
4      98002    Fall                   189500.000
..       ...     ...                          ...
275    98198  Winter                   205475.000
276    98199    Fall                   525000.000
277    98199  Spring                   540000.000
278    98199  Summer                   508000.000
279    98199  Winter                   552500.000

[280 rows x 3 columns]

In [102]:
# Creating Sale price Variable -----------
df3['sale_price'] = 0

for i in range(len(df3)):
    if df3.loc[i, 'price'] >= float(df4[(df4['zipcode'] == df3['zipcode'][i]) & (df4['season'] == df3['season'][i])]['median_price_zipcode_season']):
        df3.loc[i, 'sale_price'] = 1.1* df3['price'][i]
    else:
        df3.loc[i, 'sale_price'] = 1.3* df3['price'][i]
        

In [103]:
# Calculating the profit
df3['profit'] = df3['sale_price'] - df3['price']

In [104]:
df3['profit'].sum()

760693197.9000001

In [105]:
df3

index          id       date       price  bedrooms  bathrooms  \
0          0  7129300520 2014-10-13  221900.000         3      1.000   
1          1  4060000240 2014-06-23  205425.000         2      1.000   
2          3  2976800796 2014-09-25  236000.000         3      1.000   
3          4  6874200960 2015-02-27  170000.000         2      1.000   
4          5  4268200055 2015-05-01  245000.000         3      1.750   
...      ...         ...        ...         ...       ...        ...   
10708  21600  3025300225 2014-10-31 1450000.000         5      2.750   
10709  21601  2470200020 2014-05-14 1880000.000         4      2.750   
10710  21603  3625049079 2014-08-01 1350000.000         3      2.000   
10711  21605  5427100150 2014-06-26 1410000.000         4      2.250   
10712  21612  3262300818 2015-02-27 1865000.000         4      3.750   

       sqft_living  sqft_lot  floors  waterfront  ...  month  year  season  \
0             1180      5650   1.000           0  ...     10  2014    Fall   
1              880      6780   1.000           0  ...      6  2014  Summer   
2             1300      5898   1.000           0  ...      9  2014    Fall   
3              860      5265   1.000           0  ...      2  2015  Winter   
4             1740     11547   1.000           0  ...      5  2015  Spring   
...            ...       ...     ...         ...  ...    ...   ...     ...   
10708         3090     19865   1.000           0  ...     10  2014    Fall   
10709         3260     19542   1.000           0  ...      5  2014  Spring   
10710         2070      9600   1.000           0  ...      8  2014  Summer   
10711         3250     16684   2.000           0  ...      6  2014  Summer   
10712         3790      8797   2.000           0  ...      2  2015  Winter   

           old  basement  is_waterfront  median_price  status  sale_price  \
0      >= 1955        No             No    278277.000     buy  244090.000   
1       < 1955        No             No    278277.000     buy  267052.500   
2      >= 1955        No             No    278277.000     buy  259600.000   
3       < 1955        No             No    278277.000     buy  221000.000   
4       < 1955        No             No    278277.000     buy  269500.000   
...        ...       ...            ...           ...     ...         ...   
10708   < 1955        No             No   1892500.000     buy 1595000.000   
10709  >= 1955       Yes             No   1892500.000     buy 2068000.000   
10710   < 1955       Yes             No   1892500.000     buy 1485000.000   
10711  >= 1955        No             No   1892500.000     buy 1551000.000   
10712  >= 1955       Yes             No   1892500.000     buy 2051500.000   

          profit  
0      22190.000  
1      61627.500  
2      23600.000  
3      51000.000  
4      24500.000  
...          ...  
10708 145000.000  
10709 188000.000  
10710 135000.000  
10711 141000.000  
10712 186500.000  

[10713 rows x 32 columns]

# 7. Testing the hypothesis

## H1: Imóveis que possuem vista para água são 30% mais caros na média.

In [106]:
water_front_df = df[['price', 'waterfront']].groupby('waterfront').mean().reset_index()
water_front_df

waterfront       price
0           0  531563.600
1           1 1661876.025

## Calculating the diference on the mean:

In [107]:
def diff_mean(val1, val2):
    percent = round(100*(val2 - val1)/val1,2)
    return percent

In [108]:
val1 = df[df['waterfront']==0]['price'].mean()
val2 = df[df['waterfront']==1]['price'].mean()
diff_mean(val1, val2)

212.64

## Plotting

In [109]:
import plotly.graph_objects as go

y0 = df[df['waterfront']==0]['price']
y1 = df[df['waterfront']==1]['price']

fig = go.Figure()
fig.add_trace(go.Box(y=y0, name='Not Waterfront',
                marker_color = 'indianred'))
fig.add_trace(go.Box(y=y1, name = 'Waterfront',
                marker_color = 'lightseagreen'))

fig.show()

- **Conclusion**: False. In average, waterfront properties are 212.64\% more expensive than the others. The mean price of waterfront proporties is `U$` 1,661,876.03 while the mean price of properties with no waterfront is `U$` 531,563.60

## H2: Imóveis com data de construção menor que 1955, são 50% mais baratos, na média.

In [110]:
df[['price', 'old']].groupby('old').mean().reset_index()

old      price
0   < 1955 537050.908
1  >= 1955 541299.968

In [111]:
val1 = df[df['old']=='< 1955']['price'].mean()
val2 = df[df['old']!='< 1955']['price'].mean()
diff_mean(val1, val2)

0.79

In [112]:
import plotly.graph_objects as go
import numpy as np

y0 = df[df['old']=='< 1955']['price']
y1 = df[df['old']!='< 1955']['price']

fig = go.Figure()
fig.add_trace(go.Box(y=y0, name='< 1955',
                marker_color = 'indianred'))
fig.add_trace(go.Box(y=y1, name = '≥ 1955',
                marker_color = 'lightseagreen'))
fig.update_layout(
    title="Prices per Year built",
    xaxis_title="Year built",
    yaxis_title="Price"
)

fig.show()

- **Conclusion**: False. In average, "new" properties (year built >= 1955) are only 0.79\% more expensive than the old ones (year built < 1955). The mean price of the old proporties is `U$` 537,050.91 while the mean price of new properties is `U$` 541,299.97.

## H3: Imóveis sem porão possuem área total (sqft_lot) que são 40% maiores do que os imóveis com porão.

In [113]:
df[['sqft_lot', 'basement']].groupby('basement').mean().reset_index()

basement  sqft_lot
0       No 16284.177
1      Yes 13286.295

In [114]:
val1 = df[df['basement']=='Yes']['sqft_lot'].mean()
val2 = df[df['basement']=='No']['sqft_lot'].mean()
diff_mean(val1, val2)

22.56

In [115]:
y0 = df[df['basement']=='Yes']['sqft_lot']
y1 = df[df['basement']=='No']['sqft_lot']
fig = go.Figure()
fig.add_trace(go.Box(y=y0, name='Yes',
                marker_color = 'indianred'))
fig.add_trace(go.Box(y=y1, name = 'No',
                marker_color = 'lightseagreen'))
fig.update_layout(
    title="Area per Basement",
    xaxis_title="Basement",
    yaxis_title="Area (sqft)"
)

fig.show()

- **Conclusion**: False. Although the proporties without basement are slightly bigger, they are only 22.56% bigger, not 40%. In average, properties without basement has area 16,284.18 square feet. Properties with basement has an area, in average, of  13,286.30 square feet. 

## H4: O crescimento do preço dos imóveis YoY (Year Over Year) é de 10%



In [116]:
df[['price', 'year']].groupby('year').mean().reset_index()

year      price
0  2014 539181.428
1  2015 541988.992

In [117]:
mean_price_2014 = df[df['year']==2014]['price'].mean()
mean_price_2015 = df[df['year']==2015]['price'].mean()
print(diff_mean(mean_price_2014, mean_price_2015))

# Standard deviation
std_price_2014 = df[df['year']==2014]['price'].std()
std_price_2015 = df[df['year']==2015]['price'].std()


0.52


In [118]:
import plotly.graph_objects as go

fig = go.Figure()
fig.add_trace(go.Bar(
    name='2014',
    x=['Year'], y=[mean_price_2014],
    error_y=dict(type='data', array=[std_price_2014])
))
fig.add_trace(go.Bar(
    name='2015',
    x=['Year'], y=[mean_price_2015],
    error_y=dict(type='data', array=[std_price_2015])
))
fig.update_layout(barmode='group')
fig.show()

- **Conclusion**: False. The YOY growth was only 0.52% between 2014 and 2015. 

## H5: Imóveis com 3 banheiros tem um crescimento de preço MoM (Month over Month) de 15%.

- Filtrar os imóveis com 3 banheiros e salvar na base de dados: three_bathrooms_df
- Calcular a média de preço da base de dados three_bathrooms_df agrupada por meses
- Calcular os crescimentos MoM
- Criar uma visualização de linhas e pontos mostrando o crescimento por mês

In [119]:
three_bathrooms_df = df[df['bathrooms']==3][['price', 'month']].groupby('month').mean().reset_index()
print(three_bathrooms_df)

    month      price
0       1 672923.171
1       2 696714.422
2       3 768495.096
3       4 709751.988
4       5 689252.100
5       6 775057.564
6       7 741405.043
7       8 737576.562
8       9 645246.887
9      10 645523.015
10     11 679910.465
11     12 728341.188


In [120]:
# Calculating MoM Growth
MoM=[]
for i in range(1,11):
    val1=three_bathrooms_df.loc[i-1,'price']
    val2=three_bathrooms_df.loc[i,'price']
    result=diff_mean(val1, val2)
    MoM.append(result) 
print(MoM)

[3.54, 10.3, -7.64, -2.89, 12.45, -4.34, -0.52, -12.52, 0.04, 5.33]


In [121]:
# Mean MoM Growth
mean(MoM)

0.3750000000000001

In [122]:
import plotly.express as px
fig = px.line(three_bathrooms_df, x='month', y='price')
fig.show()

- **Conclusion**: False. The average MoM growth was only 0.375%. 

## H6: Imóveis são reformados, em média, após 30 anos da data de construção.

In [123]:
renovated_df = df[df['yr_renovated'] != 0].copy().reset_index()
renovated_df['time_diff'] = renovated_df['yr_renovated'] - renovated_df['yr_built']
mean(renovated_df['time_diff'])

56.29978118161926

In [124]:
fig = px.histogram(renovated_df, x="time_diff")
fig.show()

- **Conclusion**: False. Properties are renovated, in average, 56.3 years after they are built.

## H7: A área dos imóveis YoY (Year Over Year) é 5% menor. 

In [125]:
area_by_year_df = df[['yr_built', 'sqft_lot']].groupby('yr_built').mean().reset_index()
area_by_year_df.head()

yr_built  sqft_lot
0      1900 10869.598
1      1901  4142.931
2      1902  4766.519
3      1903  6364.565
4      1904  5410.000

In [126]:
# Calculating YoY_area Growth
YoY_area=[]
for i in range(1, len(area_by_year_df['sqft_lot'])):
    val1=area_by_year_df.loc[i-1,'sqft_lot']
    val2=area_by_year_df.loc[i,'sqft_lot']
    result=diff_mean(val1, val2)
    YoY_area.append(result) 
#print(YoY_area)
print('Mean YoY growth in area: ' + str(round(mean(YoY_area),2)) + '%')

Mean YoY growth in area: 7.23%


In [127]:
fig = px.line(area_by_year_df, x='yr_built', y='sqft_lot')
fig.show()

**Conclusion**: FALSE. There is an average increase of 7.23% in the area of the proporties over the years.

## H8: Os imóveis são 20%  mais baratos no inverno.

In [128]:
fig = px.box(df, x="season", y="price")
fig.show()

- Calcular as estatísticas descritivas do preço por estação do ano.

In [129]:
price_season_df = df[['price', 'season']].groupby('season').mean().reset_index()
price_season_df

season      price
0    Fall 529161.322
1  Spring 558081.050
2  Summer 540114.835
3  Winter 521194.659

In [130]:
val1=df[df['season']=='Fall']['price'].mean()
val2=df[df['season']=='Winter']['price'].mean()
res1 = diff_mean(val1, val2)


val1=df[df['season']=='Spring']['price'].mean()
val2=df[df['season']=='Winter']['price'].mean()
res2 = diff_mean(val1, val2)


val1=df[df['season']=='Summer']['price'].mean()
val2=df[df['season']=='Winter']['price'].mean()
res3 = diff_mean(val1, val2)

winter_diff = [res1, res2, res3]
print(winter_diff)

print('Mean price difference in the Winter: '+ str(round(mean(winter_diff),2)) + '%')

[-1.51, -6.61, -3.5]
Mean price difference in the Winter: -3.87%


**Conclusion**: FALSE. Although the prices show to be smaller in the winter, they are only 3.87% smaller, on average, not 20%. 

## H9: No verão o lucro de vendas é 35% maior que no inverno.

In [131]:
profit_by_season_df = df3[['profit', 'season']].groupby('season').mean().reset_index()
profit_by_season_df

season    profit
0    Fall 69685.617
1  Spring 73085.284
2  Summer 71852.681
3  Winter 67900.183

In [133]:
fig = px.box(df3, x="season", y="profit")
fig.show()

In [134]:
val1 = int(profit_by_season_df[profit_by_season_df['season'] == "Winter"]['profit'])
val2 = int(profit_by_season_df[profit_by_season_df['season'] == "Summer"]['profit'])
diff_mean(val1, val2)

5.82

**Conclusion:** FALSE. The profit is 5.82% bigger in the Summer than in the Winter. 

## H10: A área de imóveis com waterfront é 25% maior que a área dos imóveis sem waterfront.

In [135]:
area_by_waterfront_df = df[['sqft_lot', 'waterfront']].groupby('waterfront').mean().reset_index()
area_by_waterfront_df

waterfront  sqft_lot
0           0 15028.964
1           1 25371.828

In [136]:
fig = px.box(df, x="waterfront", y="sqft_lot")
fig.show()

In [137]:
val1=area_by_waterfront_df['sqft_lot'][0]
val2=area_by_waterfront_df['sqft_lot'][1]
diff_mean(val1, val2)

68.82

**Conclusion:** FALSE. The total area of waterfront properties are 68.82% bigger than the area of not waterfron ones.

# 8. Mapa com as sugestões de imóveis para compra

In [138]:
df3

index          id       date       price  bedrooms  bathrooms  \
0          0  7129300520 2014-10-13  221900.000         3      1.000   
1          1  4060000240 2014-06-23  205425.000         2      1.000   
2          3  2976800796 2014-09-25  236000.000         3      1.000   
3          4  6874200960 2015-02-27  170000.000         2      1.000   
4          5  4268200055 2015-05-01  245000.000         3      1.750   
...      ...         ...        ...         ...       ...        ...   
10708  21600  3025300225 2014-10-31 1450000.000         5      2.750   
10709  21601  2470200020 2014-05-14 1880000.000         4      2.750   
10710  21603  3625049079 2014-08-01 1350000.000         3      2.000   
10711  21605  5427100150 2014-06-26 1410000.000         4      2.250   
10712  21612  3262300818 2015-02-27 1865000.000         4      3.750   

       sqft_living  sqft_lot  floors  waterfront  ...  month  year  season  \
0             1180      5650   1.000           0  ...     10  2014    Fall   
1              880      6780   1.000           0  ...      6  2014  Summer   
2             1300      5898   1.000           0  ...      9  2014    Fall   
3              860      5265   1.000           0  ...      2  2015  Winter   
4             1740     11547   1.000           0  ...      5  2015  Spring   
...            ...       ...     ...         ...  ...    ...   ...     ...   
10708         3090     19865   1.000           0  ...     10  2014    Fall   
10709         3260     19542   1.000           0  ...      5  2014  Spring   
10710         2070      9600   1.000           0  ...      8  2014  Summer   
10711         3250     16684   2.000           0  ...      6  2014  Summer   
10712         3790      8797   2.000           0  ...      2  2015  Winter   

           old  basement  is_waterfront  median_price  status  sale_price  \
0      >= 1955        No             No    278277.000     buy  244090.000   
1       < 1955        No             No    278277.000     buy  267052.500   
2      >= 1955        No             No    278277.000     buy  259600.000   
3       < 1955        No             No    278277.000     buy  221000.000   
4       < 1955        No             No    278277.000     buy  269500.000   
...        ...       ...            ...           ...     ...         ...   
10708   < 1955        No             No   1892500.000     buy 1595000.000   
10709  >= 1955       Yes             No   1892500.000     buy 2068000.000   
10710   < 1955       Yes             No   1892500.000     buy 1485000.000   
10711  >= 1955        No             No   1892500.000     buy 1551000.000   
10712  >= 1955       Yes             No   1892500.000     buy 2051500.000   

          profit  
0      22190.000  
1      61627.500  
2      23600.000  
3      51000.000  
4      24500.000  
...          ...  
10708 145000.000  
10709 188000.000  
10710 135000.000  
10711 141000.000  
10712 186500.000  

[10713 rows x 32 columns]

## 8.1. Filtros

- Waterfront
- Preço
- Número de quartos
- Número de banheiros


In [139]:
type(df['price'].min())

float

In [140]:
import pandas as pd
import ipywidgets as widgets
from ipywidgets import fixed
import plotly.express as px

# Interactive buttons
price_filter = widgets.FloatSlider(
    value = df3['price'].mean(),
    min = df3['price'].min(),
    max = df3['price'].max(),
    description = 'Price Limit: ',
    disable = False,
    readout=True
)

waterfront_filter = widgets.Dropdown(
    options=df3['is_waterfront'].unique().tolist(),
    value='No',
    description='Waterview?',
    disable=False
)

bedrooms_filter = widgets.Dropdown(
    options=sorted(df3['bedrooms'].unique().tolist()),
    value=0,
    description='# Bedrooms: ',
    disable=False
)

bathrooms_filter = widgets.Dropdown(
    options=sorted(df3['bathrooms'].unique().tolist()),
    value=0,
    description='# Bathrooms: ',
    disable=False
)

# Function to update map based on filters selction
def update_map(df3, waterfront, price_limit, bedrooms, bathrooms):
    
    houses = df3[(df3['price'] <= price_limit) &
                (df3['is_waterfront'] == waterfront) &
                (df3['bedrooms'] == bedrooms) &
                (df3['bathrooms'] == bathrooms)][['id', 'lat', 'long', 'price', 'profit']] 
    
    fig = px.scatter_mapbox(houses,
                           lat='lat',
                           lon='long',
                           color='price',
                           size='profit',
                           color_continuous_scale=px.colors.sequential.Inferno,
                           size_max=15,
                           zoom=10)
    
    fig.update_layout(mapbox_style='open-street-map')
    fig.update_layout(height=600, margin={'r':0, 't':0, 'l':0, 'b':0})
    fig.show()



In [141]:
widgets.interactive(update_map, df3=fixed(df3),
                    price_limit=price_filter,
                   bedrooms=bedrooms_filter,
                   bathrooms=bathrooms_filter,
                   waterfront=waterfront_filter)


interactive(children=(Dropdown(description='Waterview?', options=('No', 'Yes'), value='No'), FloatSlider(value…